In [273]:
%matplotlib inline
import sys
import string
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import arff
import random

from sklearn import tree
from sklearn import linear_model
from sklearn.externals.six import StringIO
from sklearn.cross_validation import train_test_split
from IPython.core.display import Image

import pydot

# Load the Data

In [219]:
%%time
gender = {'Male' : 0, 'Female' : 1, 'Unknown' : 2}
language = {'English' : 0, 'EnglishandAnother' : 1, 'Another' : 2}

trainfile = 'sample_data\\test05.arff'

examples = []
features = []
labels = []

with open(trainfile, 'rb') as af:
    arffFile = arff.load(af)
    # do not include college gpa and college credits
    features = [arffFile['attributes'][0:-3][i][0].encode("ascii") for i in range(len(arffFile['attributes'][0:-3]))]
    data = arffFile['data']
    for row in data:
        row[0] = gender[row[0]] # index of gender
        row[12] = language[row[12]] # index of language
        examples.append(row[0:-3]) # do not include number of credits taken first year
        labels.append(row[-1])
        
print 'Number of examples:', len(examples)

Number of examples: 2801
Wall time: 100 ms


# Decision Tree

In [220]:
%%time
dt = tree.DecisionTreeClassifier()
dt.fit_transform(examples, labels)
print dt

DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=None,
            max_features=None, max_leaf_nodes=None, min_samples_leaf=1,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            random_state=None, splitter='best')
Wall time: 22 ms


In [221]:
%%time
dot_data = StringIO()
tree.export_graphviz(dt, out_file=dot_data, feature_names=features) 
#tree.export_graphviz(dt, out_file=dot_data) 
graph = pydot.graph_from_dot_data(dot_data.getvalue()) 
treepng = graph.create_png()

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.870814 to fit

Wall time: 9.06 s


In [222]:
Image(treepng)

In [223]:
%%time
with open('tree_SATACT.png', 'wb') as f:
    f.write(treepng)

Wall time: 16 ms


# Evaluate Tree on Test Set

In [224]:
%%time
trainfile = 'sample_data\\train05.arff'

testexamples = []
testlabels = []

with open(trainfile, 'rb') as af:
    arffFile = arff.load(af)
    # do not include college gpa and college credits
    features = [arffFile['attributes'][0:-3][i][0].encode("ascii") for i in range(len(arffFile['attributes'][0:-3]))]
    data = arffFile['data']
    for row in data:
        row[0] = gender[row[0]] # index of gender
        row[12] = language[row[12]] # index of language
        testexamples.append(row[0:-3]) # do not include number of credits taken first year
        testlabels.append(row[-1])

Wall time: 0 ns


In [225]:
%%time
numCorrect = 0
numIncorrect = 0
testCount = len(testexamples)
for index in range(testCount):
    x = testexamples[index]
    if dt.predict(x) == testlabels[index]:
        numCorrect += 1
    else:
        numIncorrect += 1
print 'Correctly Classified:', numCorrect
print 'Incorrectly Classified:', numIncorrect
print 'Error: %f' % (float(numCorrect) / float(testCount) * 100)

Correctly Classified: 58
Incorrectly Classified: 24
Error: 70.731707
Wall time: 0 ns


# Using Raw Data Ranges

In [277]:
%%time
trainfile = 'sample_data\\rawTrain_norm.arff'

examples = []
features = []
labels = []

with open(trainfile, 'rb') as af:
    arffFile = arff.load(af)
    # do not include college gpa and college credits
    features = [arffFile['attributes'][0:-3][i][0].encode("ascii") for i in range(len(arffFile['attributes'][0:-3]))]
    data = arffFile['data']
    for row in data:
        row[0] = gender[row[0]] # index of gender
        row[12] = language[row[12]] # index of language
        examples.append(row[0:-3]) # do not include number of credits taken first year
        labels.append(row[-1])
        
print 'Number of examples:', len(examples)

Number of examples: 2952
Wall time: 182 ms


In [278]:
%%time
dt = tree.DecisionTreeClassifier()
dt = dt.fit(examples, labels)
print dt.feature_importances_

[ 0.00599366  0.00435955  0.02361286  0.08538787  0.01899501  0.03335335
  0.03441995  0.03022911  0.01863956  0.0226044   0.65817105  0.03064015
  0.00678495  0.02680851]
Wall time: 24 ms


In [279]:
%%time
dot_data = StringIO()
tree.export_graphviz(dt, out_file=dot_data, feature_names=features) 
#tree.export_graphviz(dt, out_file=dot_data) 
graph = pydot.graph_from_dot_data(dot_data.getvalue()) 
treepng = graph.create_png()

Wall time: 8.78 s


In [280]:
Image(treepng)

In [281]:
%%time
with open('tree_range.png', 'wb') as f:
    f.write(treepng)

Wall time: 0 ns


In [282]:
%%time
trainfile = 'sample_data\\rawTest_norm.arff'

testexamples = []
testlabels = []

with open(trainfile, 'rb') as af:
    arffFile = arff.load(af)
    # do not include college gpa and college credits
    features = [arffFile['attributes'][0:-3][i][0].encode("ascii") for i in range(len(arffFile['attributes'][0:-3]))]
    data = arffFile['data']
    for row in data:
        row[0] = gender[row[0]] # index of gender
        row[12] = language[row[12]] # index of language
        testexamples.append(row[0:-3]) # do not include number of credits taken first year
        testlabels.append(row[-1])

Wall time: 0 ns


In [283]:
%%time
numCorrect = 0
numIncorrect = 0
testCount = len(testexamples)
for index in range(testCount):
    x = testexamples[index]
    if dt.predict(x) == testlabels[index]:
        numCorrect += 1
    else:
        numIncorrect += 1
print 'Correctly Classified:', numCorrect
print 'Incorrectly Classified:', numIncorrect
print 'Error: %f' % (float(numCorrect) / float(testCount) * 100)

Correctly Classified: 35
Incorrectly Classified: 15
Error: 70.000000
Wall time: 2 ms


In [284]:
%%time
score = dt.score(testexamples, testlabels)
print score

0.7
Wall time: 0 ns


# Transform features

In [300]:
%%time
dt = tree.DecisionTreeClassifier()
dt.fit(examples, labels)
x2 = dt.transform(examples)

# hard coding feature extraction indexeseseses
first = 3
second = 10

print x2
print 'before:', dt.feature_importances_
dt.fit(x2, labels)
print 'after:', dt.feature_importances_

[[ 0.625     0.780991]
 [ 0.75      0.054853]
 [ 0.428571  0.054853]
 ..., 
 [ 0.392857  0.019963]
 [ 0.642857  0.671487]
 [ 0.375     0.019963]]
before: [ 0.00641811  0.00470278  0.03020245  0.08207961  0.02228879  0.03449328
  0.03103691  0.02478247  0.01883969  0.02016089  0.65598716  0.03261344
  0.00794573  0.02844868]
after: [ 0.18073137  0.81926863]
Wall time: 22 ms


In [288]:
%%time
dot_data = StringIO()
tree.export_graphviz(dt, out_file=dot_data, feature_names=features)
graph = pydot.graph_from_dot_data(dot_data.getvalue()) 
treepng = graph.create_png()

Wall time: 7.85 s


In [289]:
Image(treepng)

In [290]:
%%time
with open('tree_range_lessfeatures.png', 'wb') as f:
    f.write(treepng)

Wall time: 1e+03 µs


# Score Feature Extraction

In [304]:
x2_test = [[x[first], x[second]] for x in testexamples]
print x2_test

[[0.803571, 0.74449], [0.928571, 0.066539], [0.535714, 0.066539], [0.821429, 0.671487], [0.75, 0.780991], [0.357143, 0.488979], [0.392857, 0.671487], [0.5, 0.066539], [0.696429, 0.066539], [0.525223, 0.671487], [0.892857, 0.066539], [0.525223, 0.488979], [0.452059, 0.488979], [0.303571, 0.306472], [0.678571, 0.634985], [0.928571, 0.027877], [0.642857, 0.671487], [0.660714, 0.027877], [0.839286, 0.027877], [0.589286, 0.74449], [0.357143, 0.488979], [0.452059, 0.634985], [0.5, 0.019963], [0.464286, 0.561982], [0.464286, 0.019963], [0.36959, 0.525481], [0.339286, 0.452478], [0.214286, 0.019963], [0.232143, 0.415976], [0.714286, 0.525481], [0.36959, 0.196967], [0.5, 0.561982], [0.607143, 0.0], [0.571429, 0.0], [0.339286, 0.0], [0.553571, 0.0], [0.428456, 0.561982], [0.535714, 0.0], [0.660714, 0.598484], [0.732143, 0.0], [0.571429, 0.0], [0.589286, 0.0], [0.339286, 0.0], [0.535714, 0.634985], [0.714286, 0.780991], [0.589286, 0.561982], [0.446429, 0.415976], [0.75, 0.054853], [0.125, 0.05485

In [307]:
%%time
score = dt.score(x2_test, testlabels)
print 'Accuracy: %f' % (score * 100)

Accuracy: 68.000000
Wall time: 28 ms
